# Predicting Temperature

In this notebook, we will use gradient descent to minimize the squared error between a custom model and the (mock) temperature data gathered from sensors spread across the Winooski River valley in Vermont. Using the trained model, we will predict the temperature at a given time and location within the same region.

First, we will load the data from the Springtail dataset and display the first 10 records.

In [1]:
import psycopg2

def get_data():
    """
    Gets all temperature data from the cloud database
    """
    dbname = "temperature"
    user = "observer"
    password = "hamburger"
    host = "springtail.postgres.database.azure.com"
    port = "5432"

    connection = psycopg2.connect(dbname=dbname, user=user, password=password, host=host, port=port)
    cursor = connection.cursor()
    cursor.execute("SELECT reading_time, latitude, longitude, temperature FROM reading")
    rows = cursor.fetchall()
    cursor.close()
    connection.close()
    return rows

tuples = get_data()
print("Total number of rows: ", len(tuples))

for row_number in range(10):
    print(tuples[row_number])


Total number of rows:  89
(datetime.datetime(2025, 3, 19, 15, 28, 9, 112442), Decimal('44.262804'), Decimal('-72.571794'), Decimal('15.62'))
(datetime.datetime(2025, 3, 5, 17, 1, 16, 788710), Decimal('44.304621'), Decimal('-72.908188'), Decimal('13.43'))
(datetime.datetime(2025, 3, 5, 17, 1, 31, 843459), Decimal('44.304621'), Decimal('-72.908188'), Decimal('12.74'))
(datetime.datetime(2025, 3, 5, 17, 1, 46, 862259), Decimal('44.304621'), Decimal('-72.908188'), Decimal('14.22'))
(datetime.datetime(2025, 3, 5, 17, 15, 17, 113578), Decimal('44.304621'), Decimal('-72.908188'), Decimal('14.24'))
(datetime.datetime(2025, 3, 5, 17, 15, 32, 129316), Decimal('44.304621'), Decimal('-72.908188'), Decimal('13.68'))
(datetime.datetime(2025, 3, 5, 17, 15, 47, 140732), Decimal('44.304621'), Decimal('-72.908188'), Decimal('13.56'))
(datetime.datetime(2025, 3, 5, 17, 16, 2, 152227), Decimal('44.304621'), Decimal('-72.908188'), Decimal('12.89'))
(datetime.datetime(2025, 3, 5, 17, 16, 17, 163774), Decima

The model we will use with have a sinusoidal shape in the time-of-day dimension and a planar shape in the two spatial dimensions. The model will have six parameters: three for the sinusoidal shape (amplitude $a$, frequency $\omega$, and phase $\phi$), and three for the plane ($c_1$, $c_2$, and $c_3$).

$$ \text{temperature} = - a \cdot \cos(2\pi \cdot \omega \cdot \text{time} + \phi) + (c_1 \cdot \text{latitude} + c_2 \cdot \text{longitude} + c_3) $$ 

Time is a value between 0 and 1.0, representing the fraction of the day that has elapsed (e.g., 0.5 is noon). It is computed from the hours, minutes, and seconds of the time a reading was taken. The latitude and longitude are the coordinates of the sensor that took the reading. We will not bother with any normalization of this data for this exercise.

In [2]:
import numpy as np

# Initial values for the model parameters
a     = 5.0  # Amplitude of +/- 5 degrees
omega = 1.0  # 1 cycle per day
phi   = 0.0  # No phase shift (warmest at exactly noon)
c1    = -5.0 # Latitude effect of 5 degrees per 1 degree latitude (decreasing with increasing latitude)
c2    = -3.0 # Longitude effect of 3 degrees per 1 degree longitude (decreasing with increasing longitude)
c3    = 10.0 # Constant offset of 10 degrees

def model(time, latitude, longitude):
    temperature = -a * np.cos(2.0 * np.pi * omega * time + phi) + (c1 * latitude + c2 * longitude + c3)
    return temperature

Next, let's try a couple of sample locations with the initial model parameters to see if the values are at least within reason.

In [3]:
time = np.array([0.25, 0.5, 0.75, 1.0])   # 6am, 12pm, 6pm, 12am
latitude  =  44.341504   # Waterbury
longitude = -72.759281   # Waterbury

print("Temperatures in Waterbury over the day: ", model(time, latitude, longitude))

time = 0.5   # 12pm
latitude = np.array([44.0, 44.1, 44.2, 44.3, 44.4, 44.5])  # 44.0 to 44.5 degrees
longitude = -72.759281

print("Temperatures on S/N line through Waterbury: ", model(time, latitude, longitude))

time = 0.5   # 12pm
latitude = 44.341504  # Waterbury
longitude = np.array([-72.5, -72.6, -72.7, -72.8, -72.9, -73.0])  # 72.5 to 73.0 degrees

print("Temperatures on E/W line through Waterbury: ", model(time, latitude, longitude))

Temperatures in Waterbury over the day:  [ 6.570323 11.570323  6.570323  1.570323]
Temperatures on S/N line through Waterbury:  [13.277843 12.777843 12.277843 11.777843 11.277843 10.777843]
Temperatures on E/W line through Waterbury:  [10.79248 11.09248 11.39248 11.69248 11.99248 12.29248]


These numbers seem reasonable. However, we will use gradient descent to find the optimal parameters for the model. Note that the constant $c_3$ is a reasonable looking value because $c_1 \cdot \text{latitude}$ and $c_2 \cdot \text{longitude}$ tend to cancel out. In the final version of the model, $c_3$ may look a little strange because it will need to absorb whatever leftovers result from latitude and longitude terms.

Next we need to define the error function that we'll use as a goodness-of-fit function. We'll use the RMS error between the measured data and what the model predicts.

In [4]:
# Computes the root mean square error between the measured and predicted temperatures.
def rms_error(measured_temperature, predicted_temperature):
    return np.sqrt(np.mean((measured_temperature - predicted_temperature)**2))

# Computes the predicted temperature for the given measured data.
# The data is a 2D array with the columns: time, latitude, longitude.
def compute_predicted(measured_data):
    predicted_temperature = np.zeros(measured_data.shape[0])
    predicted_temperature = model(time=measured_data[:,0], latitude=measured_data[:,1], longitude=measured_data[:,2])
    return predicted_temperature

# Example usage of the functions.
measured_data = np.array([(0.25, 44.341504, -72.759281),
                          (0.50, 44.341504, -72.759281),
                          (0.75, 44.341504, -72.759281),
                          (1.00, 44.341504, -72.759281)])

measured_temperature = np.array([10.5, 15.3, 11.2, 4.3])  # Just an example.

predicted_temperature = compute_predicted(measured_data)
print("Measured temperature: ", measured_temperature)
print("Predicted temperature: ", predicted_temperature)
print("RMS error: ", rms_error(measured_temperature, predicted_temperature))

Measured temperature:  [10.5 15.3 11.2  4.3]
Predicted temperature:  [ 6.570323 11.570323  6.570323  1.570323]
RMS error:  3.815687929368539


Next, we need to massage the "real" data into a form that will be acceptable to `compute_predicted`.

In [5]:
def time_as_fraction(date_and_time):
    time = (date_and_time.hour + date_and_time.minute / 60.0 + date_and_time.second / 3600.0) / 24.0
    return time

raw_time        = np.array([time_as_fraction(row[0]) for row in tuples])
raw_latitude    = np.array([float(row[1]) for row in tuples])
raw_longitude   = np.array([float(row[2]) for row in tuples])
raw_temperature = np.array([float(row[3]) for row in tuples])

measured_data = np.column_stack((raw_time, raw_latitude, raw_longitude))
print(measured_data)


[[  0.64454861  44.262804   -72.571794  ]
 [  0.70921296  44.304621   -72.908188  ]
 [  0.70938657  44.304621   -72.908188  ]
 [  0.70956019  44.304621   -72.908188  ]
 [  0.71894676  44.304621   -72.908188  ]
 [  0.71912037  44.304621   -72.908188  ]
 [  0.71929398  44.304621   -72.908188  ]
 [  0.71946759  44.304621   -72.908188  ]
 [  0.7196412   44.304621   -72.908188  ]
 [  0.71981481  44.304621   -72.908188  ]
 [  0.71998843  44.304621   -72.908188  ]
 [  0.72016204  44.304621   -72.908188  ]
 [  0.72033565  44.304621   -72.908188  ]
 [  0.72050926  44.304621   -72.908188  ]
 [  0.72068287  44.304621   -72.908188  ]
 [  0.72085648  44.304621   -72.908188  ]
 [  0.72103009  44.304621   -72.908188  ]
 [  0.7212037   44.304621   -72.908188  ]
 [  0.72137731  44.304621   -72.908188  ]
 [  0.72155093  44.304621   -72.908188  ]
 [  0.72172454  44.304621   -72.908188  ]
 [  0.72189815  44.304621   -72.908188  ]
 [  0.72207176  44.304621   -72.908188  ]
 [  0.72224537  44.304621   -72.90

Now we are ready to compute the RMS error between our (initial) model and the "real" data.

In [6]:
predicted_temperature = compute_predicted(measured_data)
print("Measured temperature: ", raw_temperature)
print("Predicted temperature: ", predicted_temperature)
print("RMS error: ", rms_error(raw_temperature, predicted_temperature))

Measured temperature:  [15.62 13.43 12.74 14.22 14.24 13.68 13.56 12.89 13.97 13.33 12.55 14.28
 13.32 12.45 13.72 13.69 12.74 13.93 12.45 12.68 13.   12.71 12.27 12.32
 12.93 13.33 13.04 12.17 13.42 13.87 12.68 12.53 13.18 13.31 12.8  12.24
 12.28 13.38 13.21 12.18 13.41 13.51 12.92 12.72 13.48 13.31 13.5  13.03
 12.6  13.55 14.02 13.02 13.84 12.12 12.22 13.47 13.47 13.19 12.49 12.7
 12.06 12.45 13.72 12.97 13.21 12.34 13.64 13.61 13.14 12.02 13.56 17.54
 16.95 16.89 17.31 17.37 16.37 16.64 16.48 16.38 17.31 16.18 16.35 16.62
 17.42 17.11 17.22 17.49 16.68]
Predicted temperature:  [ 9.47708996  8.46884184  8.46356505  8.45828677  8.17084727  8.16549602
  8.16014364  8.15479011  8.14943544  8.14407965  8.13872274  8.13336471
  8.12800558  8.12264534  8.117284    8.11192157  8.10655807  8.10119348
  8.09582782  8.0904611   8.08509332  8.0797245   8.07435462  8.06898371
  8.06361176  8.05823879  8.0528648   8.04748979  8.04211378  8.03673677
  8.03135877  8.02597977  8.0205998   8.015218

Finally, we are ready to use gradient descent to tune the parameters of the model to minimize the RMS error. Since the parameters will range over widely different scales, it is important to scale them into a similar range.

In [7]:
def real_to_scaled(real_value, min_value, max_value):
    return (real_value - min_value) / (max_value - min_value)

def scaled_to_real(scaled_value, min_value, max_value):
    return scaled_value * (max_value - min_value) + min_value

# Now we define min and max values of the various model parameters in the order a, omega, phi, c1, c2, c3.
min_values = np.array([ 0.0, 0.8, -0.5, -5.0, -5.0, -20.0])
max_values = np.array([10.0, 1.2,  0.5,  5.0,  5.0,  20.0])

# Now scale the initial model parameters.
model_parameters = np.array([a, omega, phi, c1, c2, c3])
scaled_initial_parameters = real_to_scaled(model_parameters, min_values, max_values)
print("Initial parameters: ", model_parameters)
print("Scaled initial parameters: ", scaled_initial_parameters)

Initial parameters:  [ 5.  1.  0. -5. -3. 10.]
Scaled initial parameters:  [0.5  0.5  0.5  0.   0.2  0.75]


Now we are ready to start investigating the shape of the model.

In [8]:
step_size = 0.001  # In the scaled space.
scaled_parameters = scaled_initial_parameters
for i in range(10):
    # Current values of the model parameters.
    a, omega, phi, c1, c2, c3 = scaled_to_real(scaled_parameters, min_values, max_values)
    predicted_temperature = compute_predicted(measured_data)
    print("RMS error:", rms_error(raw_temperature, predicted_temperature), "| Parameters:", a, omega, phi, c1, c2, c3)

    # Compute the gradient of the loss function.
    gradient = np.zeros(6)
    for i in range(6):
        scaled_parameters[i] += step_size
        a, omega, phi, c1, c2, c3 = scaled_to_real(scaled_parameters, min_values, max_values)
        predicted_temperature = compute_predicted(measured_data)
        loss_plus = rms_error(raw_temperature, predicted_temperature)
        scaled_parameters[i] -= 2 * step_size
        a, omega, phi, c1, c2, c3 = scaled_to_real(scaled_parameters, min_values, max_values)
        predicted_temperature = compute_predicted(measured_data)
        loss_minus = rms_error(raw_temperature, predicted_temperature)
        gradient[i] = (loss_plus - loss_minus) / (2 * step_size)
        scaled_parameters[i] += step_size

    # Update the parameters.
    scaled_parameters -= step_size * (gradient/np.abs(gradient))

    #if np.sum(np.abs(gradient)) < 0.0001:
    #    break


RMS error: 5.526968245601073 | Parameters: 5.0 1.0 0.0 -5.0 -3.0 10.0
RMS error: 4.322013681053094 | Parameters: 5.01 0.9996 -0.0010000000000000009 -4.99 -3.01 10.04
RMS error: 3.1340185432730587 | Parameters: 5.02 0.9992 -0.0020000000000000018 -4.98 -3.02 10.079999999999998
RMS error: 1.9936134853152092 | Parameters: 5.03 0.9988 -0.0030000000000000027 -4.97 -3.03 10.120000000000001
RMS error: 1.0664778564905457 | Parameters: 5.04 0.9984 -0.0040000000000000036 -4.96 -3.04 10.16
RMS error: 1.1449964114379196 | Parameters: 5.05 0.998 -0.0050000000000000044 -4.95 -3.05 10.2
RMS error: 1.0664778564905457 | Parameters: 5.04 0.9984 -0.0040000000000000036 -4.96 -3.04 10.16
RMS error: 1.1449964114379196 | Parameters: 5.05 0.998 -0.0050000000000000044 -4.95 -3.05 10.2
RMS error: 1.0664778564905457 | Parameters: 5.04 0.9984 -0.0040000000000000036 -4.96 -3.04 10.16
RMS error: 1.1449964114379196 | Parameters: 5.05 0.998 -0.0050000000000000044 -4.95 -3.05 10.2
